In [1]:
import pandas as pd


# Tool from text processing  
import nltk
from nltk.corpus import stopwords

# Tool  
import spacy
import pandas as pd

# Regual expressions
import re

df = pd.read_csv("OpenAi/amlo_clasify_chatpgt3.csv")

stop_words_es = stopwords.words('spanish')


nlp = spacy.load('es_core_news_lg')


def return_dataframe():

    df['cla_num'] = df['Clasificacion'].apply(clasification_to_num)
    df['Texto_limpio'] = df['Texto'].apply(clean_text)
    return df



# fn to clean text 

def clean_text(texto):
  textofin = texto.lower()
  textofin = re.sub(r'([^0-9A-Za-z-À-ÿ \t])','', textofin,)
  textofin = nlp(textofin)
  lema = []
  for token in textofin:
    lema.append(token.lemma_)

  textofin = lema
  textofin = ' '.join(textofin)
  return textofin
  
def clasification_to_num(text):
    if text == 'exterior':
        return 0
    elif text == 'economia':
        return 1
    elif text == 'opinion' :
        return 2
    elif text == 'competencia':
        return 3
    elif text == 'apoyo':
        return 4
    elif text == 'seguridad':
        return 5
  


df["clean"] = df["Texto"].apply(clean_text)



In [5]:
import joblib
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.linear_model import LogisticRegression
from sklearn.manifold import TSNE
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.svm import SVC
tfidf = TfidfVectorizer(ngram_range=(1, 3))

X = df["clean"]
y = df["classification_spanish"]
X_train, X_test, y_train, y_test = train_test_split(
    X, y, train_size=0.97, random_state=42
)
X_train_vec = tfidf.fit_transform(X_train)
X_test_vec = tfidf.transform(X_test)
model = LogisticRegression(multi_class="multinomial", solver="sag")
model.fit(X_train_vec, y_train)
y_pred = model.predict(X_test_vec)
report = classification_report(y_test, y_pred, output_dict=True)
clasification = pd.DataFrame(report).transpose()
clasification.to_csv("Lregresion/clasification2.csv")

joblib.dump(model, "Lregresion/LogisticRegresion2.joblib")
joblib.dump(tfidf, "Lregresion/tfidf_vectorizer2.joblib")

def predict_text(text):
    resultado = clean_text(text)
    resultado = tfidf.transform([resultado])
    prediccion = model.predict(resultado)
    probabilida = model.predict_proba(resultado)
    print(probabilida)
    return probabilida


def match_category(category):
    match category:
        case "0":
            return "apoyo"
        case "1":
            return "competencia"
        case "2":
            return "construccion"
        case "3":
            return "corrupcion"
        case "4":
            return "economia"
        case "5":
            return "exterior"
        case "6":
            return "historia"
        case "7":
            return "opinion"
        case "8": 
            return "salud"
        case "9":
            return "seguridad"
        case _:
            return category
def match_category2(category):
    match category:
        case 0:
            return "apoyo"
        case 1:
            return "competencia"
        case 2:
            return "construccion"
        case 3:
            return "corrupcion"
        case 4:
            return "economia"
        case 5:
            return "exterior"
        case 6:
            return "historia"
        case 7:
            return "opinion"
        case 8: 
            return "salud"
        case 9:
            return "seguridad"


def predict(proba):
    proba = list(proba[0])
    print(proba)
    maxx = max(proba)
    index = proba.index(maxx)
    return f"La probabilidad es {maxx} y lo categoriza como {match_category2(index)}"


def clasification_rep():
    clasification["Unnamed: 0"] = clasification["Unnamed: 0"].astype(str)

    clasification["Unnamed: 0"] = clasification["Unnamed: 0"].apply(match_category)
    a = clasification.rename(columns={"Unnamed: 0": "Clasificación", "precision" : "Precision"})

    return a


first = predict_text("Adultos mayores")

df.head()

print(predict(first))

print(clasification)




[[7.68609141e-01 4.36636718e-02 2.30166698e-02 1.47137936e-02
  1.44417662e-02 1.10824948e-02 1.09785214e-02 9.21148232e-02
  1.66042725e-04 8.23963673e-03 1.29734385e-02]]
[0.7686091412426548, 0.043663671847752106, 0.023016669780122605, 0.014713793601158567, 0.014441766213273697, 0.011082494772357676, 0.010978521425687972, 0.09211482317757352, 0.00016604272513426734, 0.008239636725486518, 0.012973438488798339]
La probabilidad es 0.7686091412426548 y lo categoriza como apoyo
              precision    recall  f1-score      support
apoyo          0.541667  0.406250  0.464286   128.000000
competencia    0.382253  0.486957  0.428298   230.000000
construccion   0.586777  0.710000  0.642534   100.000000
corrupcion     0.640625  0.405941  0.496970   101.000000
economia       0.710526  0.435484  0.540000    62.000000
exterior       0.627451  0.457143  0.528926    70.000000
historia       0.526316  0.169492  0.256410    59.000000
opinion        0.385027  0.562500  0.457143   256.000000
salud  

In [5]:

first = predict_text("Vamos, como lo hacemos todos lunes, a informar quién es quién en los precios, también el avance en las obras, el avance en la construcción del aeropuerto de Santa Lucía, el avance en la construcción de la refinería de Dos Bocas.")



print(predict(first))

[[4.04802358e-07 4.65235489e-07 9.99451418e-01 9.89789909e-06
  3.25592431e-04 2.14661747e-05 1.98501383e-05 1.30873649e-05
  6.89197121e-05 1.18848489e-05 7.70129315e-05]]
[4.048023582290229e-07, 4.6523548908093876e-07, 0.9994514184619914, 9.897899088706479e-06, 0.0003255924306322247, 2.1466174706003473e-05, 1.985013834271561e-05, 1.3087364908048738e-05, 6.891971211436844e-05, 1.1884848906935497e-05, 7.701293146257646e-05]
La probabilidad es 0.9994514184619914 y lo categoriza como construccion


In [2]:
import nltk
from nltk.corpus import stopwords

# Tool  
import spacy
import pandas as pd

# Regual expressions
import re

df = pd.read_csv("OpenAi/amlo_clasify_chatpgt3.csv")

stop_words_es = stopwords.words('spanish')


nlp = spacy.load('es_core_news_lg')


def return_dataframe():
    df['cla_num'] = df['classification_spanish'].apply(clasification_to_num)
    df['Texto_limpio'] = df['Texto'].apply(clean_text)
    return df



# fn to clean text 

def clean_text(texto):
  textofin = texto.lower()
  textofin = re.sub(r'([^0-9A-Za-z-À-ÿ \t])','', textofin,)
  textofin = nlp(textofin)
  lema = []
  for token in textofin:
    lema.append(token.lemma_)
  textofin = lema
  textofin = ' '.join(textofin)
  return textofin
  
def clasification_to_num(text):
    if text == 'apoyo':
        return 0
    elif text == 'competencia':
        return 1
    elif text == 'construccion' :
        return 2
    elif text == 'corrupcion':
        return 3
    elif text == 'economia':
        return 4
    elif text == 'exterior':
        return 5
    elif text == 'historia':
        return 6
    elif text == 'opinion':
        return 7
    elif text == 'salud':
        return 8
    elif text == 'seguridad':
        return 9 

df = return_dataframe()
df.head()

Texto Clasificacion  \
0   Buenos días y feliz año. Deseamos que nos vay...       saludos   
1  Vamos a iniciar la semana como lo hacemos siem...           NaN   
2  También vamos a informar este primer día hábil...         apoyo   
3  Y ahora se va a informar porque se está optand...         apoyo   
4  En esta etapa se combinan los bancos particula...         apoyo   

  new_classification classification_spanish  cla_num  \
0            Support                  apoyo      0.0   
1             Health                  salud      8.0   
2            Support                  apoyo      0.0   
3            Support                  apoyo      0.0   
4            Support                  apoyo      0.0   

                                        Texto_limpio  
0    buen día y feliz año desear que yo ir bien a...  
1  ir a iniciar el semana como él hacer siempre e...  
2  también ir a informar este primero día hábil d...  
3  y ahora él ir a informar porque él estar optar...  
4  en este etapa él combinar el banco particular ...

In [4]:
# Tool
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.manifold import TSNE
from sklearn.model_selection import train_test_split

import pandas as pd
import plotly.express as px

from Models2 import text_pro


# apply the fn to the dataframe 

tsne_result_df  =  pd.read_csv("TSNe/tsne_results2.csv")
def plot_tsne():
  fig = px.scatter(data_frame = tsne_result_df,
                  x = tsne_result_df['tsne_1'],
                  y = tsne_result_df['tsne_2'],
                  color = tsne_result_df['label'],
                  template = 'plotly_dark',
                  hover_data = ['text'])
  return fig
plot_tsne().show()